In [ ]:
from datetime import datetime
import MetaTrader5 as mt5
import pandas as pd
import matplotlib.pyplot as plt

pd.set_option('display.max_columns', 500) # number of columns to be displayed
pd.set_option('display.width', 1500)      # max table width to display
 
# establish connection to MetaTrader 5 terminal
if not mt5.initialize(login=********, server="MetaQuotes-Demo",password="********")
    print("initialize() failed, error code =",mt5.last_error())
    quit()
 
# get 250 D1 bars from the current day
xauusd_rates = mt5.copy_rates_from_pos("XAUUSD", mt5.TIMEFRAME_D1, 0, 250)
xaueur_rates = mt5.copy_rates_from_pos("XAUEUR", mt5.TIMEFRAME_D1, 0, 250)
xauaud_rates = mt5.copy_rates_from_pos("XAUAUD", mt5.TIMEFRAME_D1, 0, 250)
xauchf_rates = mt5.copy_rates_from_pos("XAUCHF", mt5.TIMEFRAME_D1, 0, 250)
xaugbp_rates = mt5.copy_rates_from_pos("XAUGBP", mt5.TIMEFRAME_D1, 0, 250)
# get 250 D1 bars from the current day for EURUSD
eurusd_rates = mt5.copy_rates_from_pos("EURUSD", mt5.TIMEFRAME_D1, 0, 250)

# shut down connection to the MetaTrader 5 terminal
mt5.shutdown()

# create DataFrame out of the obtained data
xauusd_frame = pd.DataFrame(xauusd_rates)
xaueur_frame = pd.DataFrame(xaueur_rates)
xauaud_frame = pd.DataFrame(xauaud_rates)
xauchf_frame = pd.DataFrame(xauchf_rates)
xaugbp_frame = pd.DataFrame(xaugbp_rates)
# include the EURUSD data in the DataFrame
eurusd_frame = pd.DataFrame(eurusd_rates)

# convert time in seconds into the datetime format
xauusd_frame['time']=pd.to_datetime(xauusd_frame['time'], unit='s')
xaueur_frame['time']=pd.to_datetime(xaueur_frame['time'], unit='s')
xauaud_frame['time']=pd.to_datetime(xauaud_frame['time'], unit='s')
xauchf_frame['time']=pd.to_datetime(xauchf_frame['time'], unit='s')
xaugbp_frame['time']=pd.to_datetime(xaugbp_frame['time'], unit='s')
# include the EURUSD data in the DataFrame
eurusd_frame['time']=pd.to_datetime(eurusd_frame['time'], unit='s') 
 
# display dataframe with OHLC data
# print("\nDisplay dataframe with data")
# print(xauusd_frame)
# print(xaueur_frame) 

# display close data
xauusd_close = xauusd_frame[['time','close']]
xaueur_close = xaueur_frame[['time','close']]
xauaud_close = xauaud_frame[['time','close']]
xauchf_close = xauchf_frame[['time','close']]
xaugbp_close = xaugbp_frame[['time','close']]
# include the EURUSD data in the DataFrame
eurusd_close = eurusd_frame[['time','close']]
# print("\nDisplay close data")
print(xauusd_close)
print(xaueur_close)

# print(xaueur_close)
# xauusd_close.plot(x='time', y='close', style='r-', label='XAUUSD')
# plt.show()

In [ ]:
# calculate correlation coefficients
import numpy as np
usd_eur_corr = np.corrcoef(xauusd_close['close'], xaueur_close['close'])
usd_aud_corr = np.corrcoef(xauusd_close['close'], xauaud_close['close'])
usd_chf_corr = np.corrcoef(xauusd_close['close'], xauchf_close['close'])
usd_gbp_corr = np.corrcoef(xauusd_close['close'], xaugbp_close['close'])
# print correlation coefficients
# print(usd_eur_corr, usd_aud_corr, usd_chf_corr, usd_gbp_corr)
# print(usd_aud_corr)
# print(usd_chf_corr)
# print(usd_gbp_corr)

In [ ]:
# plot close data for XAUUSD and XAUEUR
# xauusd_close.plot(x='time', y='close', style='r-', label='XAUUSD')
# xaueur_close.plot(x='time', y='close', style='b-', label='XAUEUR')
joined = xauusd_close.merge(xaueur_close, on='time', suffixes=('_xauusd', '_xaueur'))
joined.plot(title='One Year of XAUUSD and XAUEUR (D1)', x='time', y=['close_xauusd', 'close_xaueur'])
plt.show()

In [ ]:
# joined2 = joined.merge(eurusd_close, how='inner', on='time', suffixes=(None, '_eurusd'))
adjusted_for_dollars = pd.concat([xauusd_close, xaueur_close['close'], eurusd_close['close']], join='inner', axis=1)
adjusted_for_dollars.columns = ['time', 'xauusd', 'xaueur', 'eurusd']
adjusted_for_dollars['xaueur_dollars'] = adjusted_for_dollars['xaueur'] * adjusted_for_dollars['eurusd']
adjusted_for_dollars['diff'] = abs(adjusted_for_dollars['xauusd'] - adjusted_for_dollars['xaueur_dollars'])

print(adjusted_for_dollars)
adjusted_for_dollars.plot(title = 'One Year of XAUUSD and XAUEUR in US Dollars (D1)', x='time', y=['xauusd', 'xaueur_dollars'])
plt.show()
# joined2.plot(title='Pearson Price Correlation', x='time', y=['close_xauusd', 'close_xaueur', 'close_eurusd'])
# plt.show()

In [ ]:
print("median: ", adjusted_for_dollars['diff'].median())
adjusted_for_dollars['diff'].describe()